In [ ]:
# import PyRosetta library
from pyrosetta import *
init()

# download a PDB from RCSB
from pyrosetta.toolbox import pose_from_rcsb

In [ ]:
pose = pose_from_rcsb("1ubq")

# declare scorefunction with which we're minimizing
scorefxn = get_fa_scorefxn()

# declare DOFs we want to allow to minimize
mm = MoveMap()
mm.set_bb(True)
mm.set_chi(True)

# minimize options
min_mover = rosetta.protocols.minimization_packing.MinMover()
min_mover.movemap(mm)
min_mover.score_function(scorefxn)
min_mover.min_type("lbfgs_armijo")
min_mover.tolerance(1e-6)

# do the minimization
pose.dump_pdb("/home/dimaio/Downloads/1ubq_before_min.pdb")
scorefxn.show(pose)
min_mover.apply(pose)
scorefxn.show(pose)
pose.dump_pdb("/home/dimaio/Downloads/1ubq_after_min.pdb")

In [ ]:
# minimize with a subset of DOFs
def min_pose(pose, scorefxn, mm):
    min_mover = rosetta.protocols.minimization_packing.MinMover()
    min_mover.movemap(mm)
    min_mover.score_function(scorefxn)
    min_mover.min_type("lbfgs_armijo")
    min_mover.tolerance(1e-6)
    min_mover.apply(pose)

pose = pose_from_rcsb("1ubq")
scorefxn = get_fa_scorefxn()

# declare DOFs we want to allow to minimize
mm = MoveMap()
for i in range(1,10):
    mm.set_bb(i,True)
    mm.set_chi(i,True)

scorefxn.show(pose)
min_pose(pose,scorefxn,mm)
scorefxn.show(pose)
pose.dump_pdb("/home/dimaio/Downloads/1ubq_after_submin.pdb")

In [ ]:
# Cartesian-space minimization
pose = pose_from_rcsb("1ubq")
scorefxn = rosetta.core.scoring.ScoreFunctionFactory.create_score_function("ref2015_cart.wts")

mm = MoveMap()
mm.set_bb(True)
mm.set_chi(True)

min_mover = rosetta.protocols.minimization_packing.MinMover()
min_mover.movemap(mm)
min_mover.score_function(scorefxn)
min_mover.min_type("lbfgs_armijo")
min_mover.tolerance(1e-6)
min_mover.cartesian(True)

scorefxn.show(pose)
min_mover.apply(pose)
scorefxn.show(pose)

pose.dump_pdb("/home/dimaio/Downloads/1ubq_after_cartmin.pdb")

In [ ]:
# relax mover : combines packing and minimization
scorefxn = get_fa_scorefxn()
pose = pose_from_rcsb("1ubq")
fastrelax = rosetta.protocols.relax.FastRelax(scorefxn, 1) # 1 => # of macrocycles
fastrelax.apply(pose)
pose.dump_pdb("/home/dimaio/Downloads/1ubq_relaxed.pdb")

In [ ]:
scorefxn.show(pose)

In [ ]:
# constraints: adding user-defined constraints to a pose
def add_cst(pose, res_i, atm_i, res_j, atm_j):
    id_i = AtomID(pose.residue(res_i).atom_index(atm_i),res_i)
    id_j = AtomID(pose.residue(res_j).atom_index(atm_j),res_j)
    
    ijfunc = rosetta.core.scoring.constraints.BoundFunc(0.0, 1.8, 0.1, 'cst1')
    cst_ij = rosetta.core.scoring.constraints.AtomPairConstraint(
            id_i, id_j, ijfunc
    )
    pose.add_constraint(cst_ij)

pose = pose_from_sequence("AAAAAA")
pose.dump_pdb("/home/dimaio/Downloads/A6_initial.pdb")

add_cst(pose,2,"H",5,"O")
add_cst(pose,2,"O",5,"H")

scorefxn = rosetta.core.scoring.ScoreFunctionFactory.create_score_function("ref2015_cst.wts")
scorefxn.show(pose)

In [ ]:
# relax with constraints
pose = pose_from_sequence("AAAAAA")
add_cst(pose,2,"H",5,"O")
add_cst(pose,2,"O",5,"H")
fastrelax = rosetta.protocols.relax.FastRelax(scorefxn, 4)
fastrelax.apply(pose)
pose.dump_pdb("/home/dimaio/Downloads/A6_relaxed.pdb")

In [ ]:
scorefxn.show(pose)